In [1]:
def printBoard(board, chamberWidth=7):
    n = len(board)
    for i in range(n - 1, -1, -1):
        row = "".join(["#" if board[i][j] else "." for j in range(chamberWidth)])
        print(f"|{row}|")
    print(f"+{'-' * chamberWidth}+")


In [2]:
from itertools import cycle

# rock shapes
# ####
#
# .#.
# ###
# .#.
#
# ..#
# ..#
# ###
#
# #
# #
# #
# #
#
# ##
# ##
rockShapes = [
    ["1111"],
    ["010", "111", "010"],
    ["001", "001", "111"],
    ["1", "1", "1", "1"],
    ["11", "11"],
]

with open("17.input", "r") as f:
    line = f.read().rstrip()
    # line = ">>><<><>><<<>><>>><<<>>><<<><<<>><>><<>>"
    # "<": -1, ">": 1
    jetPattern = map(lambda x: -1 if x == "<" else 1, line)


def validMove(board, i, j, rock):
    height = len(rock)
    width = len(rock[0])
    if i - height + 1 < 0 or j < 0 or j + width - 1 > len(board[0]) - 1:
        return False
    for k, row in enumerate(rock):
        for l, c in enumerate(row):
            if c == "1" and i - k < len(board) and board[i - k][j + l] == "1":
                return False
    return True


jet = cycle(enumerate(jetPattern))
shape = cycle(enumerate(rockShapes))
chamberWidth = 7
# initial board, board[0] is the bottom row
board = [["0"] * chamberWidth for _ in range(3)]
highestRock = -1  # the highest row have a rock in the board
# maxNumRocks = 2022 # for part 1

maxNumRocks = 1000000000000  # for part 2
seen = {}
numRowsToCache = 30
rowsHidden = 0

for numRocks in range(maxNumRocks):
    rockIdx, rock = next(shape)
    height = len(rock)
    # worst case: the rock stops right above the hightest rock
    if len(board) <= highestRock + height:
        # extend by the height of the highest rock
        board.extend([["0"] * chamberWidth for _ in range(4)])
    # top left corner of the rock
    i, j = highestRock + 3 + height, 2
    landed = False
    cached = False

    # The first cycle begins at the 299th rock, and the cycle length is 1755
    # (569800569, 1106) = divmod(1000000000000 - 299, 1755),
    # so we need to know the height increasd from the cycle begin till 1106 rocks
    # 1106 + 299 = 1405
    if numRocks == 1405:
        print(highestRock + 1 + rowsHidden)
    while not landed:
        jetIdx, jOffset = next(jet)

        # cache the top n rows of the board and check if there is a cycle
        if highestRock > numRowsToCache and not cached:
            cached = True
            boardTopRows = board[highestRock - numRowsToCache : highestRock + 1]
            boardKey = "".join(["".join(row) for row in boardTopRows])
            lastTimeSeen = seen.get((rockIdx, jetIdx, boardKey))
            if lastTimeSeen:
                # there is a cycle
                print("cycle detected", lastTimeSeen, numRocks)
                print("cycle length", numRocks - lastTimeSeen[0])
                print(
                    "cycle height increased",
                    highestRock + 1 + rowsHidden - lastTimeSeen[1],
                )
                print(rockIdx, jetIdx, boardKey)
            else:
                seen[(rockIdx, jetIdx, boardKey)] = (
                    numRocks,
                    highestRock + 1 + rowsHidden,
                )

        if validMove(board, i, j + jOffset, rock):
            j += jOffset
        iOffset = -1
        if validMove(board, i + iOffset, j, rock):
            i += iOffset
        else:
            landed = True
            highestRock = max(highestRock, i)
            for row in rock:
                for k, c in enumerate(row):
                    if c == "1":
                        board[i][j + k] = "1"
                i -= 1
    # prune the board, remove oldest n rows that will never be reached
    if highestRock > 1000:
        del board[:900]
        highestRock -= 900
        rowsHidden += 900

    # printBoard(board)
print(highestRock + 1 + rowsHidden, len(board))


2194
cycle detected (299, 449) 2054
cycle length 1755
cycle height increased 2768
4 1752 0010100001110000111000111110111001001111100011110001111000111100001000001110011111100110110011000001000000100000011110001111001110100011110000111000000100000010000001000011110011101000011110001110000010000001000000100
cycle detected (300, 449) 2055
cycle length 1755
cycle height increased 2768
0 1761 0010100001110000111000111110111001001111100011110001111000111100001000001110011111100110110011000001000000100000011110001111001110100011110000111000000100000010000001000011110011101001111110111110000010000001000000100
cycle detected (301, 449) 2056
cycle length 1755
cycle height increased 2768
1 1768 0010100001110000111000111110111001001111100011110001111000111100001000001110011111100110110011000001000000100000011110001111001110100011110000111000000100000010000001000011110011101001111110111110111110000001000000100
cycle detected (302, 450) 2057
cycle length 1755
cycle height increased 2768
2 1774 00111

KeyboardInterrupt: 